## 用ROOT的tree 结构存储数据

### 中子飞行时间谱测量

闪烁体探测器长度：2L

光在闪烁体的传播速度: $v_{sc}$，光衰减常数：$\lambda$

$d=\sqrt{D^2+x^2}$

中子飞行时间：$TOF_n(ns)=\frac{72 \cdot d(m)}{\sqrt{E_n(MeV)}}$,   gamma飞行时间：$TOF_{\gamma}(ns)=3\cdot d(m)$

探测器两端时间：$t_u=TOF+x/v_{sc}$， $t_d=TOF+(2L-x)/v_{sc}$

探测器两端能量(x 处能量沉积Q)：$Q_u=Q_0 exp[-x/\lambda]$， $Q_d=Q_0 exp[-(2L-x)/\lambda]$

<img src="tof.png" width="50%" height="50%">

### 用ROOT的tree 结构存储数据
``` cpp

// 将下列代码保存到tree.cc
// 在ROOT环境中运行：
// .L tree.cc
// 生成 tree.root 文件
void tree(){
  const Double_t nD=500;//cm, distance between target and the scin.(Center)
  const Double_t nL=100;//cm, half length of the scin.
  const Double_t nTh=5;//cm, thickness of the scin.
  const Double_t ts=1;//ns, sigma of time of the scin.
  const Double_t lambda=380;//cm, attenuation lenght of the scin.
  const Double_t Qs=0.1;//relative energy resolution of the scin. 
  const Double_t vsc=7.5//ns/cm, speed of light in the scin.
  const Double_t En0=50;//MeV, average neutron energy
  const Double_t Ens=10;//MeV, sigma of En
  const Double_t Eg0=1;//MeV, gamma energy  
  const Double_t rgamma=0.3;//ratio of gamma 
      
  TFile *opf=new TFile("tree.root","recreate");//新文件tree.root的指针 *opf
  TTree *opt=new TTree("tree","tree structure");//新tree的指针 *opt
  // 在tree结构中定义需要的变量分支
  Double_t x;
  Double_t E;
  int ng;
  Double_t TOF, nTOF;
  Double_t tu, td;
  Double_t Qu, Qd;
 
  // 将变量分支添加到tree结构中,第一个参数为变量名称，第二个为上面定义的变量地址，第三个为变量的类型说明，D表示Double_t。
  opt->Branch("x", &x, "x/D");//position of neutron
  opt->Branch("E", &E, "E/D");//energy of gamma or neutron
  opt->Branch("TOF", &TOF, "TOF/D");//time of flight
  opt->Branch("nTOF",&nTOF,"nTOF/D");//TOF from exp. data
  opt->Branch("ng", &ng, "ng/D");//1/0 : neutron/gamma  
  opt->Branch("tu", &tu, "tu/D");//time of upper side
  opt->Branch("td", &td, "td/D");//time of bottom side
  opt->Branch("Qu", &Qu, "Qu/D");//Q 
  opt->Branch("Qd", &Qd, "Qd/D");//Q  
  // histogram
   TH1D *hnTOF=new TH1D("hnTOF","neutron time of flight",1000,0,100);//文件中还可存储histogram，graph等
  TRandom *gr=new TRandom(0);
  // 循环，逐事件往tree结构里添加对应分支信息。
  for(int i=0;i<100000;i++){
    x=gr->Uniform(-nL, nL);
    Double_t D=nD+gr->Uniform(-0.5,0.5)*nTh;
    Double_t d=TMath::Sqrt(D*D+x*x)*0.01;//m, flight path
    if(gr->Uniform() < rgamma) { //gamma
       ng=0;
       E=gr->Uniform()*Eg0;
       TOF=3*d;
    }
    else {  //neutron
        ng=1;
        E=gr->Gaus(En0, Ens); // neutron
        TOF=72./TMath::Sqrt(E)*d;
    }
    tu=TOF+x/vsc+gr->Gaus(0,ts);
    td=TOF+(2*nL-x)/vsc+gr->Gaus(0,ts);
    nTOF=(tu+td)/2.;
    hnTOF->Fill(nTOF);
    Qu=E*TMath::Exp(-x/lambda);
    Qu=gr->Gaus(Qu,Qs*Qu);
    Qd=E*TMath::Exp(-(2L-x)/lambda);
    Qd=gr->Gaus(Qd,Qs*Qd);
    opt->Fill();
  }
  // 将数据写入root文件中
  hnTOF->Write();
  opt->Write();
  opf->Close();
}

```

In [1]:
%jsroot on

In [2]:
TFile *ipf=new TFile("tree.root");
ipf->ls()//ROOT 环境下 > .ls

TFile**		tree.root	
 TFile*		tree.root	
  KEY: TTree	tree;3	tree structure
  KEY: TTree	tree;2	tree structure
  KEY: TH1D	hnTOF;1	neutron time of flight


In [3]:
tree->Print()

******************************************************************************
*Tree    :tree      : tree structure                                         *
*Entries :  1000000 : Total =        72094538 bytes  File  Size =   67419788 *
*        :          : Tree compression factor =   1.07                       *
******************************************************************************
*Br    0 :x         : x/D                                                    *
*Entries :  1000000 : Total  Size=    8010329 bytes  File Size  =    7056028 *
*Baskets :      114 : Basket Size=    3200000 bytes  Compression=   1.13     *
*............................................................................*
*Br    1 :E         : E/D                                                    *
*Entries :  1000000 : Total  Size=    8010329 bytes  File Size  =    7462220 *
*Baskets :      114 : Basket Size=    3200000 bytes  Compression=   1.07     *
*...................................................

In [4]:
TCanvas *c1=new TCanvas();//* 在ROOT环境下可省略
c1->Clear();//* 在ROOT环境下可省略
tree->Draw("nTOF>>(1000,0,100)");
c1->Draw();//* 在ROOT环境下可省略

In [5]:
TH1D *hh=(TH1D*) ipf->Get("hnTOF"); //在代码中得到文件内数据指针的方法，在ROOT环境下课直接用 hnTOF->Draw()
hh->Draw();

In [6]:
c1->SetLogz();
gStyle->SetPalette(1);
tree->Draw("tu:td>>(1000,0,130,1000,0,130)","","colz");
c1->Draw();

In [7]:
tree->Draw("tu-td:x","","colz");
c1->Draw();

In [8]:
tree->Draw("tu-td:log(Qd/Qu)","","colz");
c1->Draw();